<a href="https://colab.research.google.com/github/InowaR/colab/blob/main/ParticleSimulator3D.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import time
import numpy as np
from IPython.display import clear_output
from scipy.spatial import KDTree
import random

class Particle:
    def __init__(self, x, y, z, vx, vy, vz, color):
        self.x = x
        self.y = y
        self.z = z
        self.vx = vx
        self.vy = vy
        self.vz = vz
        self.color = color

    def move(self):
        self.x += self.vx
        self.y += self.vy
        self.z += self.vz

class Simulator:
    def __init__(self, width, height, depth):
        self.width = width
        self.height = height
        self.depth = depth
        self.particles = []
        self.collision_radius = 1.5

    def add_particle(self, particle):
        self.particles.append(particle)

    def create_cube(self, start_x, start_y, start_z, width, height, depth, speed_range, color, density=1.0):
        particles = []

        for x in range(start_x, start_x + width):
            for y in range(start_y, start_y + height):
                for z in range(start_z, start_z + depth):
                    if random.random() <= density:
                        vx = random.uniform(speed_range[0], speed_range[1])
                        vy = random.uniform(speed_range[0], speed_range[1])
                        vz = random.uniform(speed_range[0], speed_range[1])
                        particles.append(Particle(x, y, z, vx, vy, vz, color))

        return particles

    def kdtree_collisions(self):
        positions = np.array([[p.x, p.y, p.z] for p in self.particles])
        tree = KDTree(positions)
        collision_pairs = tree.query_pairs(self.collision_radius)

        for i, j in collision_pairs:
            p1, p2 = self.particles[i], self.particles[j]
            distance = np.sqrt((p1.x - p2.x)**2 + (p1.y - p2.y)**2 + (p1.z - p2.z)**2)
            if distance <= 1.0:
                p1.vx, p2.vx = p2.vx, p1.vx
                p1.vy, p2.vy = p2.vy, p1.vy
                p1.vz, p2.vz = p2.vz, p1.vz

    def simulate_step(self):
        for p in self.particles:
            p.move()

            # Отражение от границ
            if p.x <= 0 or p.x >= self.width - 1:
                p.vx = -p.vx
            if p.y <= 0 or p.y >= self.height - 1:
                p.vy = -p.vy
            if p.z <= 0 or p.z >= self.depth - 1:
                p.vz = -p.vz

        self.kdtree_collisions()

def print_3d_projections(simulator):
    color_symbols = {
        'красный': '🔴',
        'синий': '🔵'
    }

    # Создаем три проекции: XY, XZ, YZ
    xy_proj = [['· ' for _ in range(simulator.width)] for _ in range(simulator.height)]
    xz_proj = [['· ' for _ in range(simulator.width)] for _ in range(simulator.depth)]
    yz_proj = [['· ' for _ in range(simulator.height)] for _ in range(simulator.depth)]

    for p in simulator.particles:
        x, y, z = int(round(p.x)), int(round(p.y)), int(round(p.z))
        symbol = color_symbols.get(p.color, '⚪')

        # XY проекция (вид сверху)
        if 0 <= x < simulator.width and 0 <= y < simulator.height:
            xy_proj[y][x] = symbol

        # XZ проекция (вид спереди)
        if 0 <= x < simulator.width and 0 <= z < simulator.depth:
            xz_proj[z][x] = symbol

        # YZ проекция (вид сбоку)
        if 0 <= y < simulator.height and 0 <= z < simulator.depth:
            yz_proj[z][y] = symbol

    print("XY проекция (вид сверху):")
    for row in xy_proj:
        print(''.join(row))

    print("\nXZ проекция (вид спереди):")
    for row in xz_proj:
        print(''.join(row))

    print("\nYZ проекция (вид сбоку):")
    for row in yz_proj:
        print(''.join(row))

def main():
    width, height, depth = 10, 10, 10

    sim = Simulator(width, height, depth)

    body_cube = sim.create_cube(
        start_x=3, start_y=3, start_z=3,
        width=5, height=3, depth=3,
        speed_range=(-0.01, 0.01),
        color='синий',
        density=1
    )

    fire_cube = sim.create_cube(
        start_x=0, start_y=0, start_z=8,
        width=10, height=10, depth=2,
        speed_range=(-0.5, 0.5),
        color='красный',
        density=0.8
    )

    for particle in fire_cube + body_cube:
        sim.add_particle(particle)

    try:
        for _ in range(1000):
            clear_output(wait=True)
            print_3d_projections(sim)
            sim.simulate_step()
            time.sleep(1)

    except KeyboardInterrupt:
        print('\nСимуляция остановлена')

if __name__ == "__main__":
    main()

XY проекция (вид сверху):
🔴🔴🔴🔴🔴· 🔴🔴🔴🔴
🔴🔴🔴🔴· 🔴🔴🔴🔴🔴
🔴🔴🔴🔴🔴🔴🔴· 🔴🔴
🔴🔴🔴🔵🔵🔵🔵🔵🔴🔴
🔴🔴🔴🔵🔵🔵🔵🔵🔴🔴
🔴🔴🔴🔵🔵🔵🔵🔵🔴· 
🔴🔴· 🔴· 🔴🔴· · · 
🔴🔴🔴🔴🔴🔴🔴· 🔴🔴
· 🔴· 🔴· 🔴🔴🔴· 🔴
🔴🔴🔴🔴🔴🔴🔴🔴🔴🔴

XZ проекция (вид спереди):
· · · · · · · · · · 
· · · · · · · · · · 
· · · · · · · · · · 
· · · 🔵🔵🔵🔵🔵· · 
· · · 🔵🔵🔵🔵🔵· · 
· · · 🔵🔵🔵🔵🔵· · 
· · · · · · · · · · 
· · 🔴🔴🔴· 🔴🔴🔴🔴
🔴🔴🔴🔴🔴🔴🔴🔴🔴🔴
🔴🔴🔴🔴🔴🔴🔴🔴🔴🔴

YZ проекция (вид сбоку):
· · · · · · · · · · 
· · · · · · · · · · 
· · · · · · · · · · 
· · · 🔵🔵🔵· · · · 
· · · 🔵🔵🔵· · · · 
· · · 🔵🔵🔵· · · · 
· · · · · · · · · · 
🔴🔴🔴· · 🔴🔴· 🔴🔴
🔴🔴🔴🔴🔴🔴🔴🔴🔴🔴
🔴🔴🔴🔴🔴🔴🔴🔴🔴🔴

Симуляция остановлена


In [67]:
import time
import numpy as np
from scipy.spatial import KDTree
import random
import plotly.graph_objects as go

class Particle:
    def __init__(self, x, y, z, vx, vy, vz, color):
        self.x = x
        self.y = y
        self.z = z
        self.vx = vx
        self.vy = vy
        self.vz = vz
        self.color = color

    def move(self):
        self.x += self.vx
        self.y += self.vy
        self.z += self.vz

class Simulator:
    def __init__(self, width, height, depth):
        self.width = width
        self.height = height
        self.depth = depth
        self.particles = []
        self.collision_radius = 1.5

    def add_particle(self, particle):
        self.particles.append(particle)

    def create_cube(self, start_x, start_y, start_z, width, height, depth, speed_range, color, density=1.0):
        particles = []

        for x in range(start_x, start_x + width):
            for y in range(start_y, start_y + height):
                for z in range(start_z, start_z + depth):
                    if random.random() <= density:
                        vx = random.uniform(speed_range[0], speed_range[1])
                        vy = random.uniform(speed_range[0], speed_range[1])
                        vz = random.uniform(speed_range[0], speed_range[1])
                        particles.append(Particle(x, y, z, vx, vy, vz, color))

        return particles

    def kdtree_collisions(self):
        positions = np.array([[p.x, p.y, p.z] for p in self.particles])
        tree = KDTree(positions)
        collision_pairs = tree.query_pairs(self.collision_radius)

        for i, j in collision_pairs:
            p1, p2 = self.particles[i], self.particles[j]
            distance = np.sqrt((p1.x - p2.x)**2 + (p1.y - p2.y)**2 + (p1.z - p2.z)**2)
            if distance <= 1.0:
                p1.vx, p2.vx = p2.vx, p1.vx
                p1.vy, p2.vy = p2.vy, p1.vy
                p1.vz, p2.vz = p2.vz, p1.vz

    def simulate_step(self):
        for p in self.particles:
            p.move()

            # Отражение от границ
            if p.x <= 0 or p.x >= self.width - 1:
                p.vx = -p.vx
            if p.y <= 0 or p.y >= self.height - 1:
                p.vy = -p.vy
            if p.z <= 0 or p.z >= self.depth - 1:
                p.vz = -p.vz

        self.kdtree_collisions()

def create_particle_animation(simulator, num_frames):
    # Сохраняем позиции частиц для всех кадров
    positions_history = []

    # Запускаем симуляцию и сохраняем позиции
    for frame in range(num_frames):
        frame_positions = []
        for p in simulator.particles:
            frame_positions.append([p.x, p.y, p.z, p.color])
        positions_history.append(frame_positions)
        simulator.simulate_step()

    # Создаем фигуру Plotly
    fig = go.Figure()

    # Цвета для частиц
    color_map = {
        'красный': 'red',
        'синий': 'blue',
    }

    # Добавляем начальные позиции частиц
    for i, particle_data in enumerate(positions_history[0]):
        x, y, z, color_name = particle_data
        color = color_map.get(color_name)

        fig.add_trace(go.Scatter3d(
            x=[x],
            y=[y],
            z=[z],
            mode='markers',
            marker=dict(size=8, color=color),
            name=f'Частица {i+1}',
            showlegend=False
        ))

    # Создаем кадры анимации
    frames = []
    for frame_idx, frame_data in enumerate(positions_history):
        frame_traces = []
        for i, particle_data in enumerate(frame_data):
            x, y, z, color_name = particle_data
            color = color_map.get(color_name)

            frame_traces.append(go.Scatter3d(
                x=[x],
                y=[y],
                z=[z],
                mode='markers',
                marker=dict(size=8, color=color),
                showlegend=False
            ))

        frames.append(go.Frame(
            data=frame_traces,
            name=str(frame_idx)
        ))

    fig.frames = frames

    # Настройка слайдера
    slider_steps = []
    for k in range(num_frames):
        slider_steps.append(
            dict(
                method="animate",
                args=[[str(k)],
                      {"frame": {"duration": 0, "redraw": True},
                       "mode": "immediate",
                       "transition": {"duration": 0}}],
                label=str(k)
            )
        )

    # Настройка кнопок управления и слайдера
    fig.update_layout(
        title="3D Визуализация столкновений частиц",
        scene=dict(
            xaxis=dict(range=[0, simulator.width], title="X"),
            yaxis=dict(range=[0, simulator.height], title="Y"),
            zaxis=dict(range=[0, simulator.depth], title="Z"),
            aspectmode='cube',
            camera=dict(
                eye=dict(x=1.5, y=1.5, z=1.5)
            )
        ),
        updatemenus=[
            dict(
                type="buttons",
                buttons=[
                    dict(label="▶️ Play",
                         method="animate",
                         args=[None, {"frame": {"duration": 50, "redraw": True},
                                     "fromcurrent": True,
                                     "transition": {"duration": 0}}]),
                    dict(label="⏸️ Pause",
                         method="animate",
                         args=[[None], {"frame": {"duration": 0, "redraw": False},
                                       "mode": "immediate",
                                       "transition": {"duration": 0}}])
                ],
                x=0.1, y=0,
                xanchor="right", yanchor="bottom"
            )
        ],
        sliders=[dict(
            steps=slider_steps,
            active=0,
            currentvalue={"prefix": "Кадр: "},
            x=0, y=0,
            len=1.0,
            xanchor="left",
            yanchor="top"
        )]
    )

    return fig

def main():
    # Параметры симуляции
    width, height, depth = 20, 20, 20

    # Создаем симулятор
    sim = Simulator(width, height, depth)

    # Создаем куб "тела" (синие частицы)
    body_cube = sim.create_cube(
        start_x=9, start_y=9, start_z=2,
        width=3, height=3, depth=3,
        speed_range=(-0.1, 0.1),
        color='синий',
        density=1
    )

    # Создаем куб "огня" (красные частицы)
    fire_cube = sim.create_cube(
        start_x=0, start_y=0, start_z=0,
        width=20, height=20, depth=1,
        speed_range=(-1, 1),
        color='красный',
        density=1
    )

    # Добавляем частицы в симулятор
    for particle in body_cube + fire_cube:
        sim.add_particle(particle)

    print(f"Всего частиц: {len(sim.particles)}")
    print("Создание анимации...")

    # Создаем анимацию
    fig = create_particle_animation(sim, num_frames=100)

    # Показываем анимацию
    fig.show()

if __name__ == "__main__":
    main()

Всего частиц: 427
Создание анимации...
